In [2]:
# 测试，自定义tool，一个输入
from langchain.agents import load_tools, AgentExecutor
from langchain.agents import AgentType
from pydantic import BaseModel, Field
from langchain.tools import Tool

class SingleInput(BaseModel):
    msg: str = Field()

def singleInputAddLizhen(msg):
    return msg+", lizhen"

singleTool = Tool.from_function(
    name = "SingleInput",
        func=singleInputAddLizhen,
        description="数字相加",
        args_schema=SingleInput,
        return_direct=False
)

singleTool.run(tool_input="22222")

'22222, lizhen'

In [3]:
# 测试，自定义tool，多个输入
from langchain.tools import StructuredTool

class MultiInput(BaseModel):
    a: int = Field()
    b: int = Field()
    
def multiInput(a, b) -> str:
    return f"result={a+b}"

multiTool = StructuredTool.from_function(
    name = "MultiInput",
        func=multiInput,
        description="多个输入，数字相加",
        args_schema=MultiInput,
        return_direct=True
)

multiTool.run(tool_input={"a":1, "b":2})

'result=3'

In [4]:
#自定义代理
from langchain.agents import Tool, AgentExecutor, BaseSingleActionAgent
from typing import List, Tuple, Any, Union
from langchain.schema import AgentAction, AgentFinish

class LizhenAgent(BaseSingleActionAgent):
    """自定义代理"""
    
    @property
    def input_keys(self):
        return ["input"]
    
    def plan(
        self,
        intermediate_steps: List[Tuple[AgentAction, str]],
        **kwargs: Any,
    ) -> Union[AgentAction, AgentFinish]:
        return AgentAction(tool="MultiInput", tool_input=kwargs["input"], log="")
    
    def aplan(
        self,
        intermediate_steps: List[Tuple[AgentAction, str]],
        **kwargs: Any,
    ) -> Union[AgentAction, AgentFinish]:
        return AgentAction(tool="MultiInput", tool_input=kwargs["input"], log="")
    
agent = LizhenAgent()
tools = [multiTool, singleTool]
agent_executor = AgentExecutor.from_agent_and_tools(agent=agent, tools=tools, verbose=True)
agent_executor.run(input={"a":1, "b":2})



> Entering new AgentExecutor chain...
result=3

> Finished chain.


'result=3'

In [5]:
from langchain.tools import tool

@tool
def tool1(event) -> str:
    """这里必须添加描述，不然AssertionError: Function must have a docstring if description not provided."""
    return f"BaseMultiActionAgent , {event}"

tool1.run("run tool1")

'BaseMultiActionAgent , run tool1'

In [6]:
from langchain.tools import tool

@tool
def tool2(event) -> str:
    """这里必须添加描述，不然AssertionError: Function must have a docstring if description not provided."""
    return f"BaseMultiActionAgent , {event}"

tool2.run("run tool2")

'BaseMultiActionAgent , run tool2'

In [7]:
#自定义代理
from langchain.agents import Tool, AgentExecutor, BaseMultiActionAgent
from typing import List, Tuple, Any, Union
from langchain.schema import AgentAction, AgentFinish

class LizhenMultiAgent(BaseMultiActionAgent):
    """自定义代理"""
    
    @property
    def input_keys(self):
        return ["input"]
    
    def plan(
        self,
        intermediate_steps: List[Tuple[AgentAction, str]],
        **kwargs: Any,
    ) -> Union[AgentAction, AgentFinish]:
        if len(intermediate_steps) == 0:
            return [AgentAction(tool="MultiInput", tool_input=kwargs["input"], log=""), AgentAction(tool="SingleInput", tool_input=kwargs["input"], log="")]
        else:
            return AgentFinish(return_values={"output": "bar"}, log="")
    def aplan(
        self,
        intermediate_steps: List[Tuple[AgentAction, str]],
        **kwargs: Any,
    ) -> Union[AgentAction, AgentFinish]:
        if len(intermediate_steps) == 0:
            return [AgentAction(tool="MultiInput", tool_input=kwargs["input"], log=""), AgentAction(tool="SingleInput", tool_input=kwargs["input"], log="")]
        else:
            return AgentFinish(return_values={"output": "bar"}, log="")
    
multiAgent = LizhenMultiAgent()
multiTools = [tool1, tool2]
multi_agent_executor = AgentExecutor.from_agent_and_tools(agent=multiAgent, tools=multiTools, verbose=True)
multi_agent_executor.run(input={"a":1, "b":2})



> Entering new AgentExecutor chain...
MultiInput is not a valid tool, try another one.SingleInput is not a valid tool, try another one.

> Finished chain.


'bar'